#### Notebook for running React experiments

In [1]:
import os
os.environ['OPENAI_API_KEY'] = 'sk-proj-o5678901234567890'

In [2]:
import sys, os
sys.path.append('..')
root  = '../root/'

In [3]:
import joblib
from util import summarize_react_trial, log_react_trial, save_agents
from agents import ReactReflectAgent, ReactAgent, ReflexionStrategy

() {'temperature': 0, 'max_tokens': 250, 'stop': ['\n']} {'temperature': 0, 'max_tokens': 250, 'stop': ['\n']}
() {'temperature': 0, 'max_tokens': 250, 'stop': ['\n']} {'temperature': 0, 'max_tokens': 250, 'stop': ['\n']}
() {'temperature': 0, 'max_tokens': 100, 'stop': ['\n']} {'temperature': 0, 'max_tokens': 100, 'stop': ['\n']}
() {'temperature': 0, 'max_tokens': 100, 'stop': ['\n']} {'temperature': 0, 'max_tokens': 100, 'stop': ['\n']}
() {'temperature': 0, 'max_tokens': 250} {'temperature': 0, 'max_tokens': 250}


#### Load the HotpotQA Sample

In [4]:
hotpot = joblib.load('../data/hotpot-qa-distractor-sample.joblib').reset_index(drop = True)

#### Define the Reflexion Strategy

In [5]:
print(ReflexionStrategy.__doc__)


    NONE: No reflection
    LAST_ATTEMPT: Use last reasoning trace in context 
    REFLEXION: Apply reflexion to the next reasoning trace 
    LAST_ATTEMPT_AND_REFLEXION: Use last reasoning trace in context and apply reflexion to the next reasoning trace 
    


In [6]:
strategy: ReflexionStrategy = ReflexionStrategy.REFLEXION

#### Initialize a React Agent for each question

In [7]:
agent_cls = ReactReflectAgent if strategy != ReflexionStrategy.NONE else ReactAgent
agents = [agent_cls(row['question'], row['answer']) for _, row in hotpot.iterrows()]

/mount/mnemosyneeastus2/mnemosyne-profiling/junda/repos/reflexion/hotpotqa_runs/notebooks/../agents.py:177: LangChainDeprecationWarning: The class `DocstoreExplorer` was deprecated in LangChain 0.1.0 and will be removed in 1.0
  self.docstore = DocstoreExplorer(docstore) # Search, Lookup


#### Run `n` trials

In [8]:
n = 5
trial = 0
log = ''

In [9]:
for i in range(n):
    for agent in [a for a in agents if not a.is_correct()]:
        if strategy != ReflexionStrategy.NONE:
            agent.run(reflect_strategy = strategy)
        else:
            agent.run()
        print(f'Answer: {agent.key}')
    trial += 1
    log += log_react_trial(agents, trial)
    correct, incorrect, halted = summarize_react_trial(agents)
    print(f'Finished Trial {trial}, Correct: {len(correct)}, Incorrect: {len(incorrect)}, Halted: {len(halted)}')

> prompt(chat): Solve a question answering task with interleaving Thought, Action, Observation steps. Thought can reason about the current situation, and Action can be three types: 
(1) Search[entity], which searches the exact entity on Wikipedia and returns the first paragraph if it exists. If not, it will return some similar entities to search.
(2) Lookup[keyword], which returns the next sentence containing keyword in the last passage successfully found by Search.
(3) Finish[answer], which returns the answer and finishes the task.
You may take as many steps as necessary.
Here are some examples:
Question: What is the elevation range for the area that the eastern sector of the Colorado orogeny extends into?
Thought 1: I need to search Colorado orogeny, find the area that the eastern sector of the Colorado orogeny extends into, then find the elevation range of the area.
Action 1: Search[Colorado orogeny]
Observation 1: The Colorado orogeny was an episode of mountain building (an orogeny

< text(chat):  I need to search VIVA Media AG, find when they changed their name, then find what their new acronym stands for.
Thought 1: I need to search VIVA Media AG, find when they changed their name, then find what their new acronym stands for.
> prompt(chat): Solve a question answering task with interleaving Thought, Action, Observation steps. Thought can reason about the current situation, and Action can be three types: 
(1) Search[entity], which searches the exact entity on Wikipedia and returns the first paragraph if it exists. If not, it will return some similar entities to search.
(2) Lookup[keyword], which returns the next sentence containing keyword in the last passage successfully found by Search.
(3) Finish[answer], which returns the answer and finishes the task.
You may take as many steps as necessary.
Here are some examples:
Question: What is the elevation range for the area that the eastern sector of the Colorado orogeny extends into?
Thought 1: I need to search Color

/home/azureuser/mambaforge/envs/sglang/lib/python3.10/site-packages/wikipedia/wikipedia.py:389: GuessedAtParserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("html.parser"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 389 of the file /home/azureuser/mambaforge/envs/sglang/lib/python3.10/site-packages/wikipedia/wikipedia.py. To get rid of this warning, pass the additional argument 'features="html.parser"' to the BeautifulSoup constructor.

  lis = BeautifulSoup(html).find_all('li')


Observation 2: Could not find [Naj]. Similar: ['Naj', 'Nakhchivan International Airport', 'Naj, naj', 'Naj Razi', 'Naj Austin', 'Naj Tunich', 'Naj, Najbolja', 'Nag Hammadi', 'NAJ Cosfest', 'Hajj Naj']
> prompt(chat): Solve a question answering task with interleaving Thought, Action, Observation steps. Thought can reason about the current situation, and Action can be three types: 
(1) Search[entity], which searches the exact entity on Wikipedia and returns the first paragraph if it exists. If not, it will return some similar entities to search.
(2) Lookup[keyword], which returns the next sentence containing keyword in the last passage successfully found by Search.
(3) Finish[answer], which returns the answer and finishes the task.
You may take as many steps as necessary.
Here are some examples:
Question: What is the elevation range for the area that the eastern sector of the Colorado orogeny extends into?
Thought 1: I need to search Colorado orogeny, find the area that the eastern secto

#### Save the result log

In [11]:
with open(os.path.join(root, 'ReAct', strategy.value, f'{len(agents)}_questions_{trial}_trials.txt'), 'w') as f:
    f.write(log)
save_agents(agents, os.path.join('ReAct', strategy.value, 'agents'))

TypeError: cannot pickle '_thread.RLock' object

In [12]:
log

'\n########################################\nBEGIN TRIAL 1\nTrial summary: Correct: 33, Incorrect: 38, Halted: 29\n#######################################\n------------- BEGIN CORRECT AGENTS -------------\n\nSolve a question answering task with interleaving Thought, Action, Observation steps. Thought can reason about the current situation, and Action can be three types: \n(1) Search[entity], which searches the exact entity on Wikipedia and returns the first paragraph if it exists. If not, it will return some similar entities to search.\n(2) Lookup[keyword], which returns the next sentence containing keyword in the last passage successfully found by Search.\n(3) Finish[answer], which returns the answer and finishes the task.\nYou may take as many steps as necessary.\nQuestion: Which of Jonny Craig and Pete Doherty has been a member of more bands ?\nThought 1: I need to search Jonny Craig and Pete Doherty, find the number of bands they have been a member of, then compare.\nAction 1: Sear

In [13]:
"""
ReactQA
Finished Trial 1, Correct: 33, Incorrect: 38, Halted: 29

CotQA_context
Finished Trial 5, Correct: 73, Incorrect: 27

"""

'\nFinished Trial 1, Correct: 33, Incorrect: 38, Halted: 29\n'

In [14]:
agents